In [408]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime as dt
import folium
import folium.plugins as plugins
from sklearn.cluster import KMeans
import seaborn as sns; sns.set()
import geopy.distance

In [410]:
pd.options.display.max_rows = 100

In [238]:
file_name = "./data/2019_vy.csv"

#get DateTime on the correct format (in accordance with excel file)
def load_file(file_name):
    df = pd.read_csv(file_name)
    
    # change date format
    df['DateTime'] = pd.TimedeltaIndex(df['DateTime'], unit='d') + dt.datetime(1899,12,30)
    
    # reformat coordinates to dot-separated floats
    df['Long'] = df['Long'].apply(lambda x: float(str(x).replace(',','.')))
    df['Lat'] = df['Lat'].apply(lambda x: float(str(x).replace(',','.')))
    
    # remove outliers
    df = df[(df['Long'] <= 11) & (df['Long'] >= 10.62)]
    # only keep trip if it has a start and an end
    df = df[df.duplicated('Trip ID', keep=False)]
    return df

## Assign zone to each row

In [405]:
data = load_file(file_name)
data_copy = data[:100].copy()

lower_left = [59.855331, 10.601628]
upper_right = [59.973287, 10.950989]

zones = get_geojson_grid(upper_right, lower_left, lat_dim=26, lon_dim=40)

for zone in zones:
    upper_left = zone['features'][0]['geometry']['coordinates'][0][0]    
    upper_right = zone['features'][0]['geometry']['coordinates'][0][1]    
    lower_right = zone['features'][0]['geometry']['coordinates'][0][2]    
    lower_left = zone['features'][0]['geometry']['coordinates'][0][3]
    
    
    data_copy.loc[
        (data_copy.Long < float(upper_right[0]))
        & (data_copy.Long > float(upper_left[0]))
        & (data_copy.Lat > float(lower_left[1]))
        & (data_copy.Lat < float(upper_left[1])),'Zone'] = float(zone['Number'])
    

In [411]:
data_copy.tail(1000)

DateTime  Trip ID TripStage      Long       Lat  \
0  2018-12-31 11:39:21.888000000        1     Start  10.73382  59.92934   
1  2019-01-01 11:02:43.008000000        1       End  10.74900  59.91063   
2  2019-01-01 08:18:08.352000000        2     Start  10.73561  59.93056   
3  2019-01-01 08:42:50.976000000        2       End  10.80917  59.94132   
4  2019-01-01 14:34:39.360000000        3     Start  10.72983  59.92513   
5  2019-01-02 08:22:31.008000000        3       End  10.72983  59.92514   
6  2019-01-01 14:57:48.672000000        4     Start  10.75916  59.94318   
7  2019-01-01 15:09:32.832000000        4       End  10.76536  59.93440   
8  2019-01-01 15:09:29.376000000        5     Start  10.77465  59.91238   
9  2019-01-01 15:37:40.224000000        5       End  10.74751  59.92604   
10 2019-01-01 15:36:00.864000000        6     Start  10.79295  59.91549   
11 2019-01-01 16:11:23.712000000        6       End  10.80397  59.93507   
12 2019-01-01 16:30:50.976000000        7     Start  10.77594  59.95178   
13 2019-01-01 17:44:57.120000000        7       End  10.76939  59.95363   
14 2019-01-01 17:16:28.128000000        8     Start  10.81099  59.88066   
15 2019-01-01 18:14:10.176000000        8       End  10.81096  59.88081   
16 2019-01-01 18:10:11.712000000        9     Start  10.81094  59.88071   
17 2019-01-01 18:17:02.976000000        9       End  10.81094  59.88072   
18 2019-01-01 18:48:03.168000000       10     Start  10.80920  59.94133   
19 2019-01-01 19:08:03.264000000       10       End  10.76675  59.91313   
20 2019-01-01 19:26:04.992000000       11     Start  10.76675  59.91313   
21 2019-01-01 19:34:39.072000000       11       End  10.76675  59.91313   
22 2019-01-01 19:29:24.576000000       12     Start  10.76675  59.91313   
23 2019-01-01 19:49:18.624000000       12       End  10.80936  59.94134   
24 2019-01-01 21:20:55.392000000       13     Start  10.76408  59.91717   
25 2019-01-01 21:36:46.656000000       13       End  10.78225  59.91179   
26 2019-01-01 21:31:01.056000000       14     Start  10.74965  59.93689   
27 2019-01-01 22:06:29.952000000       14       End  10.79654  59.87715   
28 2019-01-01 22:00:27.072000000       15     Start  10.77508  59.95276   
29 2019-01-01 22:11:28.032000000       15       End  10.77523  59.95290   
30 2019-01-02 00:59:23.136000000       16     Start  10.80385  59.93503   
31 2019-01-02 01:39:25.056000000       16       End  10.79400  59.91611   
32 2019-01-02 05:38:40.416000000       17     Start  10.76557  59.93436   
33 2019-01-02 05:55:31.296000000       17       End  10.75223  59.93644   
34 2019-01-02 06:46:35.904000000       18     Start  10.75223  59.93644   
35 2019-01-02 06:57:17.856000000       18       End  10.76558  59.93437   
36 2019-01-02 07:49:33.312000000       19     Start  10.76937  59.95351   
37 2019-01-02 08:05:24.576000000       19       End  10.76937  59.95351   
38 2019-01-02 08:31:33.600000000       20     Start  10.78194  59.90066   
39 2019-01-02 08:53:58.848000000       20       End  10.76939  59.95391   
40 2019-01-02 09:23:17.088000000       21     Start  10.80910  59.94129   
41 2019-01-02 09:37:41.088000000       21       End  10.76362  59.91676   
42 2019-01-02 09:52:04.224000000       22     Start  10.76694  59.90904   
43 2019-01-02 10:53:49.920000000       22       End  10.76704  59.91114   
44 2019-01-02 10:28:33.600000000       23     Start  10.73864  59.92389   
45 2019-01-02 10:43:28.704000000       23       End  10.75568  59.92312   
46 2019-01-02 11:05:03.840000000       24     Start  10.78981  59.88349   
47 2019-01-02 11:48:22.752000000       24       End  10.79063  59.87843   
48 2019-01-02 11:45:53.280000000       25     Start  10.75568  59.92312   
49 2019-01-02 12:00:45.792000000       25       End  10.73588  59.92313   
50 2019-01-02 12:30:02.304000000       26     Start  10.76704  59.91114   
51 2019-01-02 12:40:02.784000000       26       End  10.76663  59.90898   
52 2019-01-02 14:49:01.632000000       27     Sta

In [329]:
data.head(10)

DateTime  Trip ID TripStage      Long       Lat  \
0 2018-12-31 11:39:21.888        1     Start  10.73382  59.92934   
1 2019-01-01 11:02:43.008        1       End  10.74900  59.91063   
2 2019-01-01 08:18:08.352        2     Start  10.73561  59.93056   
3 2019-01-01 08:42:50.976        2       End  10.80917  59.94132   
4 2019-01-01 14:34:39.360        3     Start  10.72983  59.92513   
5 2019-01-02 08:22:31.008        3       End  10.72983  59.92514   
6 2019-01-01 14:57:48.672        4     Start  10.75916  59.94318   
7 2019-01-01 15:09:32.832        4       End  10.76536  59.93440   
8 2019-01-01 15:09:29.376        5     Start  10.77465  59.91238   
9 2019-01-01 15:37:40.224        5       End  10.74751  59.92604   

           Car ID  Trip duration (min)  
0  V5a15A3226E5F7          1403.350000  
1  V5a15A3226E5F7          1403.350000  
2  V5a15A3226E89D            24.716667  
3  V5a15A3226E89D            24.716667  
4  V5a15A3226E999          1067.866667  
5  V5a15A3226E999          1067.866667  
6  V5a15A3226E87F            11.733333  
7  V5a15A3226E87F            11.733333  
8  V5a15A3226CA4C            28.183333  
9  V5a15A3226CA4C            28.183333

In [241]:
#nr of cars
data['Car ID'].nunique()

255

In [242]:
#Number of trips
count = len(data.index)/2
print(count)

149376.0


In [243]:
def get_start_data(df):
    return df.loc[df['TripStage'] == 'Start']

def get_end_data(df):
    return df.loc[df['TripStage'] == 'End']

In [244]:
def plot_scatter(df, n, center):
    
    #Stations in trip dataset
    m = folium.Map(center, zoom_start=11)
    # mark each station as a point
    for index, row in df.sample(n=n).iterrows():
        folium.CircleMarker([row['Lat'], row['Long']],
                            radius=3,
                            popup=str(row),
                            fill_color="#3db7e4", # divvy color
                           ).add_to(m)
    return m

In [245]:
def plot_heat_map(df):
    
    m = folium.Map([59.92934, 10.73382], zoom_start=12)

    # convert to (n, 2) nd-array format for heatmap
    trips = df[['Lat', 'Long']].sample(n=1000).values
    # plot heatmap
    m.add_child(plugins.HeatMap(trips, radius=15, blur=20))
    for row in centers:
        folium.CircleMarker([row[0], row[1]],
                            radius=10,
                            popup=str(row),color = "black",
                            fill_color="black",fill_opacity=0.7 # divvy color
                           ).add_to(m)
    return m

In [246]:
start_data = get_start_data(data)
end_data = get_end_data(data)

In [247]:
#plot_heat_map(start_data)
plot_scatter(end_data, 1000, )

TypeError: plot_scatter() missing 2 required positional arguments: 'n' and 'center'

In [248]:
plot_heat_map(end_data)

## Grid creator

In [252]:
#https://www.jpytr.com/post/analysinggeographicdatawithfolium/
def get_geojson_grid(upper_right, lower_left, lat_dim=8, lon_dim=15):
    """Returns a grid of geojson rectangles, and computes the exposure in each section of the grid based on the vessel data.

    Parameters
    ----------
    upper_right: array_like
        The upper right hand corner of "grid of grids" (the default is the upper right hand [lat, lon] of the USA).

    lower_left: array_like
        The lower left hand corner of "grid of grids"  (the default is the lower left hand [lat, lon] of the USA).

    n: integer
        The number of rows/columns in the (n,n) grid.

    Returns
    -------

    list
        List of "geojson style" dictionary objects   
    """

    all_boxes = []

    lat_steps = np.linspace(lower_left[0], upper_right[0], lat_dim+1)
    lon_steps = np.linspace(lower_left[1], upper_right[1], lon_dim+1)

    lat_stride = lat_steps[1] - lat_steps[0]
    lon_stride = lon_steps[1] - lon_steps[0]
    
    zone_counter = 1

    for lat in lat_steps[:-1]:
        for lon in lon_steps[:-1]:
           
            
            # Define dimensions of box in grid
            upper_left = [lon, lat + lat_stride]
            upper_right = [lon + lon_stride, lat + lat_stride]
            lower_right = [lon + lon_stride, lat]
            lower_left = [lon, lat]
                

            # Define json coordinates for polygon
            coordinates = [
                upper_left,
                upper_right,
                lower_right,
                lower_left,
                upper_left
            ]

            geo_json = {"type": "FeatureCollection",
                        "properties":{
                            "lower_left": lower_left,
                            "upper_right": upper_right,
                        },
                        "features":[],
                        "Number": zone_counter}


            grid_feature = {
                "type":"Feature",
                "geometry":{
                    "type":"Polygon",
                    "coordinates": [coordinates],
                }
            }

            geo_json["features"].append(grid_feature)

            all_boxes.append(geo_json)
            
            zone_counter+=1

    return all_boxes

## Printing grid on map

In [250]:
def plot_samples_on_grid(dataframe, n):
    
    lower_left = [59.855331, 10.601628]
    upper_right = [59.973287, 10.950989]
    #excluded_zones = [5, 10, 11, 12, 13, 14, 27, 28, 29, 43, 44, 61, 62, 76, 77, 90, 91, 92, 
    #                  93, 99, 100, 102, 105, 106, 107, 108, 114, 115, 116, 117, 120, 121, 122, 
    #                  123, 129, 130, 131, 132, 133, 135, 136, 137, 138, 144, 145, 146, 147, 148, 149]
    
    center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]
    
    map = plot_scatter(dataframe, n, center)

    #grid_size = int(np.sqrt(len(world.pNodes)))
    grid_size = (26,40)

    grid = get_geojson_grid(lower_left, upper_right , lat_dim=grid_size[0], lon_dim=grid_size[1])
    
    count = 0
    for i, geo_json in enumerate(grid):
        #if (i not in excluded_zones):
        gj = folium.GeoJson(geo_json,
                style_function=lambda feature: {#'fillColor': color,
                                                'color':'grey',
                                                'weight': 2,
                                                'dashArray': '5, 5',
                                                'fillOpacity': 0.1}).add_to(map)
        popup_string = "Node"+str(i)
        gj.add_child(folium.Popup(popup_string, max_width=400))

    display(map)
    
    
   
    

In [227]:
plot_samples_on_grid(data, 500)

-0.004536769230767845
-0.008734025000000756
Height of cells: 0.4958941555624817 km
Width of cells: 0.9661082940405437 km
